In [230]:
import pandas as pd
import numpy as np
import jieba
import jieba.analyse
import re
from sklearn.feature_extraction.text import CountVectorizer, HashingVectorizer, TfidfTransformer,TfidfVectorizer
 
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import KFold,StratifiedKFold
from sklearn.model_selection import train_test_split
from scipy.sparse import csr_matrix, hstack
from sklearn.metrics import f1_score,accuracy_score,classification_report
import sklearn.metrics as metrics
from sklearn import svm
from sklearn.preprocessing import LabelEncoder
from collections import Counter
import pickle as pk
from sklearn import svm
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.decomposition import TruncatedSVD
from sklearn.ensemble import GradientBoostingClassifier

In [125]:
# list datalab file
!ls ./

hhh.ipynb          output.csv         submit_example.csv 人工智障.ipynb
kkk.ipynb          stopWord.txt       test_public.csv
label_encoder.sav  submit.csv         train.csv


In [126]:
path ='./'

In [304]:
def get_data():
    train = pd.read_csv(path + 'train.csv')
    test = pd.read_csv(path + 'test_public.csv')
 
    train = train.sample(frac=1)
    train = train.reset_index(drop=True)
    
    data = pd.concat([train, test])
    
    train['multi'] = train['subject'].str.cat(train['sentiment_value'].astype('str'), sep='_')
    
    lbl =  LabelEncoder()
    lblm = MultiLabelBinarizer()
    lbl.fit(train['multi'])
    nb_classes = len(list(lbl.classes_))

    pk.dump(lbl, open('label_encoder.sav','wb'))
 
#     subject = lbl.transform(train['multi'])
 
#     y1= []
#     for i in subject:
#         y1.append(i)
    train_map = {}
    train_content = {}
    for index, d in train.iterrows():
        train_content[d['content_id']] = d['content']
        if d['content_id'] in train_map:
            train_map[d['content_id']].append(lbl.transform([d['multi']])[0])
        else:
            train_map[d['content_id']] = [lbl.transform([d['multi']])[0]]
    train_res = []
    train_label = []
    for d in train_map:
        train_res.append(train_content[d])
        train_label.append(train_map[d])
    lblm.fit(train_label)
#     print(train_label)
    train_label = lblm.transform(train_label)
#     print(train_label)

    pk.dump(lblm, open('multi_label_encoder.sav','wb'))
    
    return np.array(train_res), test['content'] , test['content_id'],np.array(train_label)


In [305]:
def processing_data(data):
    rule=re.compile("[^\u4e00-\u9fa5]")
    data=re.sub(rule,"",data)
    word = jieba.cut(data)
    return ' '.join(word)

In [306]:
def pre_process():
  
    train,test,test_id,y1 = get_data()
 
    cut_train = []
    cut_test = []
    cut_comment = []
    n_train = train.shape[0]
    
    for i in train:
        cut_comment.append(processing_data(i))
        cut_train.append(processing_data(i))
    for i in test:
        cut_comment.append(processing_data(i))
        cut_test.append(processing_data(i))
        
    print('TfidfVectorizer')
    tf = TfidfVectorizer(ngram_range=(1,2),analyzer='char')
    discuss_tf = tf.fit_transform(cut_comment)
#     print(discuss_tf)
 
    print('LSA')
    svd = TruncatedSVD(n_components=5, n_iter=7, random_state=42) 
    discuss_lsa = svd.fit_transform(discuss_tf)
    
    print('HashingVectorizer')
    ha = HashingVectorizer(ngram_range=(1,2),lowercase=False)
    discuss_ha = ha.fit_transform(cut_comment)
#     print(discuss_ha)
 
    data = hstack((discuss_tf,discuss_ha, discuss_lsa)).tocsr()
#     print(data)
 
    return data[:n_train], data[n_train:],test_id,y1

In [307]:
X,test,test_id,y1= pre_process()
N = 10
kf = StratifiedKFold(n_splits=N, random_state=2018).split(X, y1)
#print(X.shape, y1.shape)
print(kf)

/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:8: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=True'.

To retain the current behavior and silence the warning, pass sort=False

  


TfidfVectorizer
HashingVectorizer
<generator object _BaseKFold.split at 0x1195d9eb8>


In [386]:
from sklearn.linear_model import LogisticRegression
#clf = LogisticRegression(C=0.5)
clf = svm.LinearSVC(loss='hinge', tol=1e-4, C=0.6)
# from sklearn.multiclass import OneVsRestClassifier
clf = OneVsRestClassifier(svm.LinearSVC(loss='hinge', tol=1e-4, C=0.6))
# from sklearn.tree import DecisionTreeClassifier
# clf = DecisionTreeClassifier()
# from sklearn.ensemble import RandomForestClassifier
# clf = RandomForestClassifier(max_depth=30)
# from sklearn.multiclass import OutputCodeClassifier
# clf = OutputCodeClassifier(svm.LinearSVC(loss='hinge', tol=1e-4, C=0.6))
from sklearn.multiclass import OneVsOneClassifier
# clf = OneVsOneClassifier(svm.LinearSVC(loss='hinge', tol=1e-4, C=0.6))

In [387]:
y_train_oofp1 = np.zeros_like(y, dtype='float64')

y_test_oofp_1 = np.zeros((test.shape[0], 30, N))
print(y_test_oofp_1.shape)

(2364, 30, 10)


In [388]:
def micro_avg_f1(y_true, y_pred):
    return metrics.f1_score(y_true, y_pred, average='micro')

In [389]:
acc = 0
vcc = 0
for i in range(N):
    X_train, X_validate, label_1_train, label_1_validate = train_test_split(X, y1, train_size=0.8)
    print(i)
#     print(X_train)
    clf.fit(X_train, label_1_train)
    val_1 = clf.predict(X_validate)
#     y_train_oofp1[test_fold] = val_
 
    print('total_value_f1:%f' % micro_avg_f1(label_1_validate, val_1))
    vcc += micro_avg_f1(label_1_validate, val_1)
    result = clf.predict(test)
    y_test_oofp_1[:, :, i] = result
 
print(acc/N)
print(vcc/N)

/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_split.py:2026: FutureWarning: From version 0.21, test_size will always complement train_size unless both are specified.
  FutureWarning)


0
total_value_f1:0.486631
1


/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_split.py:2026: FutureWarning: From version 0.21, test_size will always complement train_size unless both are specified.
  FutureWarning)


total_value_f1:0.503072
2


/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_split.py:2026: FutureWarning: From version 0.21, test_size will always complement train_size unless both are specified.
  FutureWarning)


...

total_value_f1:0.498686
8


/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_split.py:2026: FutureWarning: From version 0.21, test_size will always complement train_size unless both are specified.
  FutureWarning)


total_value_f1:0.492562
9


/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_split.py:2026: FutureWarning: From version 0.21, test_size will always complement train_size unless both are specified.
  FutureWarning)


total_value_f1:0.511471
0.0
0.49513396845406926


In [390]:
test_id_list = []
test_id_num = []
lbl = pk.load(open('label_encoder.sav','rb'))
lblm = pk.load(open('multi_label_encoder.sav','rb'))
res_2 = []
for i in range(y_test_oofp_1.shape[0]):
    tmp = []
    for j in range(N):
        try:
            label_tmp = lbl.inverse_transform(lblm.inverse_transform(np.array([y_test_oofp_1[i, :, j]]))[0])
            for k in label_tmp:
                tmp.append(k)
        except:
            continue
    word_counts = Counter(tmp)
    yes = word_counts.most_common()
#     print(yes)
    num = 0 
    max_fre = 0
    if(len(tmp) > 10):
        print(yes)
    for j in yes:
        if(num == 0 or j[1] >= max_fre):
            res_2.append(j[0])
            test_id_list.append(test_id[i])
            num += 1
            max_fre = max(max_fre, j[1])
    test_id_num.append(num)
    print(i, num)

/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty ar

0 0
1 1
2 1
3 1
4 1
5 1
6 1
7 1
8 1
9 0
10 1
11 0
12 1
13 1
14 1
15 0
16 0
17 1
18 0
19 0
20 1
21 1
22 1
23 1
24 1
25 0
26 1
27 1
28 1
29 0
30 1
31 1
32 0
33 0
34 1
35 1
36 0
37 1
38 1
39 1
40 1
41 1
42 0
43 0
44 1
45 1
46 1
47 1
48 1
49 1
50 1
51 1
52 1
53 1
54 1
55 0
56 1
57 1
58 1
59 1
60 0
61 1
62 0
[('空间_0', 8), ('空间_1', 3)]
63 1


/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty ar

64 1
65 1
66 0
67 0
68 0
69 0
70 1
71 1
72 0
73 0
74 0
75 0
76 0
77 1
78 0
79 0
80 1
81 0
82 0
83 0
84 1
85 1
86 1
87 1
88 0
89 1
90 1
91 1
92 1
93 0
94 1
95 1
96 1
97 1
98 0
99 1
100 1
101 1
102 0
103 0
104 0
105 1
106 1
107 0
108 1
109 0
110 0
111 1
112 1
113 1
114 1
115 1
116 1
117 1
118 1
119 1
120 1


/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty ar

...

/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty ar

2201 1
2202 1
2203 0
2204 0
2205 0
2206 1
2207 1
2208 1
2209 1
2210 1
2211 1
2212 1
2213 0
2214 1
2215 1
2216 1
2217 1
2218 0
2219 0
2220 1
2221 1
[('动力_0', 10), ('配置_0', 10)]
2222 2
2223 1
2224 1
2225 1
2226 1
2227 1
2228 1
2229 1
2230 0
2231 0
2232 1
2233 1
2234 1
2235 1
2236 0
2237 0
2238 1
[('配置_0', 10), ('动力_0', 3)]
2239 1
2240 1
2241 1
2242 1
2243 1
2244 0
2245 1
2246 1
2247 1
2248 1
2249 1
2250 0
2251 1
2252 1
2253 1
2254 1
2255 1
2256 0
2257 1
2258 1
2259 1
2260 1
2261 0
2262 1
2263 1
2264 0
2265 0
2266 1
2267 1
2268 1
2269 0
2270 0
2271 0


/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty ar

2272 1
2273 1
2274 0
2275 1
2276 1
2277 1
2278 1
2279 0
2280 0
2281 1
2282 0
2283 0
[('油耗_0', 10), ('动力_0', 9)]
2284 1
2285 1
2286 1
2287 1
2288 0
2289 1
2290 1
2291 1
2292 1
2293 1
2294 1
2295 1
2296 1
2297 1
2298 0
2299 0
2300 1
2301 1
2302 1
2303 1
2304 1
2305 0
2306 0
2307 1
2308 1
2309 1
2310 0
2311 1
2312 1
2313 0
2314 1
2315 1
2316 1
2317 1
2318 1
2319 0
2320 1
2321 1
2322 1
2323 1
2324 0
2325 1
2326 0
2327 0
2328 1
2329 1
2330 0
2331 1
2332 0
2333 0
2334 1
2335 1
2336 1
2337 0
2338 0
2339 1
2340 1
2341 1
2342 1
2343 0
2344 0
2345 1
2346 0
2347 1
2348 1
2349 1
2350 1
2351 0
2352 1
2353 1
2354 1
2355 1
2356 1
2357 0
2358 1
2359 1
2360 0
2361 1
2362 1
2363 0


/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:
/Users/xuqinqi/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty ar

In [391]:
# print(len(res))
print(len(res_2))
print(len(test_id_list))

result = pd.DataFrame()
result['content_id'] = list(test_id_list)
 
res = [i.split('_')[1] for i in res_2]
res_3 = [i.split('_')[0] for i in res_2]

result['subject'] = list(res_3)
result['subject'] = result['subject']
 
result['sentiment_value'] = list(res)
result['sentiment_value'] = result['sentiment_value'].astype(int)
 
result['sentiment_word'] = ''
result.to_csv('submit.csv',index=False)

1675
1675


In [351]:
result

content_id subject  sentiment_value sentiment_word
0     XuPwKCnA2fqNh5vm      价格                0               
1     2jNbDn85goX3IuPE      价格                0               
2     hLgEADQ8sUnvGFK9      价格                0               
3     nZmM7LQsfr03wUaz      价格                0               
4     pwd8MnrthDqLZafe      价格                0               
5     cudSKGTyMLbIt8k3      价格                0               
6     U5RMQtopwFzDVxHm      价格                0               
7     Kh0ayJjuTrzwPAs1      价格                0               
8     YZovRtEAyQJgTi1I      价格                0               
9     BeSIAUzoTWH9muYl      配置                1               
10    SXYTBWg6FxuboMnd      配置                0               
11    RDgTmzW9xBfY6pGv      配置                0               
12    8cMwzsxkL4XtuDG1      配置                0               
13    MOUrvjDsIJpbw6dQ      配置               -1               
14    MOUrvjDsIJpbw6dQ      配置                0               
15    t01PVoDSd9Lsy5HN      配置                0               
16    icMQmPJA9Sv0KGTw     舒适性                0               
17    VQkjM1657sIroCf3     舒适性                0               
18    1rGSYnOx9Fb2ULQX      配置                0               
19    SgNFp8ixQX1HA64y      油耗                0               
20    sO6Ac1mThYBKyl4M      油耗               -1               
21    qIUiOxGdb0M4PQky      油耗                0               
22    6GMYQa0Ag4o9nsZ2      油耗                0               
23    6Ewe2kxO5msAg0yU      动力                0               
24    PMeBcRxizIaNmAC7      油耗               -1               
25    9x4gvon6TfN0KtqY      油耗                0               
26    Er3x8Ks6mpQqeZO0      油耗                0               
27    f5UhrHg6Zztl7VWj      动力                0               
28    fYtbApDWqzGmKX8F      动力                0               
29    YUWFxTOoZCkNzKcu     舒适性                0               
...                ...     ...              ...            ...
2509  PE5gLlduiYGTzqsn      动力                0               
2510  WgtvsofC74wOIYVb      动力                0               
2511  H8jYWQ5gMADxtmuh     舒适性                1               
2512  ouMTnWL81gZemPi9      价格                0               
2513  7pDJV8ab4NjH3r5e     舒适性                0               
2514  hGPD9vBZgR6zNV4S      动力                0               
2515  2jJXvw58LHgT3RBD      动力                0               
2516  OCkifpF73WQYjoNI      内饰                0               
2517  XrQJUSeIVhBib86Z      配置               -1               
2518  MF2yRZwkDtmozdPS      内饰               -1               
2519  Yu0EUZt54G8fiHOW      外观                0               
2520  yLhg5NmjCWat4YFV      操控                0               
2521  0GtHsUD3ikzZoX5q      油耗                0               
2522  S3dNtUixLg2uVkWD      动力                0               
2523  xJ1wWtb9TsYkKO5X     舒适性                0               
2524  lr0sCcFamRVfPHn5      油耗                0               
2525  H6y17JaXzxADtqer      操控                0               
2526  DJES3mRatNG7AMwz      配置               -1               
2527  GdPUZvlCm438WtS5      油耗               -1               
2528  m1rOC6jMweNH2Q9J      价格                0               
2529  vP56NeZdJA8jtXmF      配置                0               
2530  fQnMrWegYBvTh2Ic      动力                0               
2531  xSTt0OV9nYkb6NEa      操控                1               
2532  BfWd1cJDFQLNn3gG     安全性                0               
2533  IoKEnR3JdXu0gG4h      价格                0               
2534  4p5xbNDUMLAwvzrY      动力                0               
2535  VYJEH3N0ZkGt5Xvy     舒适性                0               
2536  VYJEH3N0ZkGt5Xvy      配置               -1               
2537  iSp7q8d4eW9honmI      动力                0               
2538  WLHp3PYJ9FvOGXE2     安全性                0               

[2539 rows x 4 columns]